!mkdir content/
%cd content
!git clone https://github.com/VikasOjha666/Data-generator-for-CRNN.git
%cd Data-generator-for-CRNN
!mkdir images/
!python3 generate_data.py --n_samples 300000  

In [1]:
import fnmatch
import cv2
import numpy as np
import string
import time

from keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.utils import Sequence

from keras.layers import Dense, LSTM, Reshape, BatchNormalization, Input, Conv2D, MaxPool2D, Lambda, Bidirectional
from keras.models import Model
from keras.activations import relu, sigmoid, softmax
import keras.backend as K
from tensorflow.keras.utils import to_categorical
from keras.callbacks import ModelCheckpoint
from keras.callbacks import EarlyStopping

import os
import tensorflow as tf
import random
import matplotlib.pyplot as plt
from PIL import Image
from sklearn.utils import shuffle
from collections import defaultdict


In [2]:
#char_list = string.ascii_letters+string.digits

punclist='.?:;"'
punclist2="-+/()[]!`,|*&^%$#@'"

#Character sets to choose from.
smallletters=string.ascii_lowercase
capitalletters=string.ascii_uppercase
digits=string.digits
char_list=smallletters#+capitalletters+digits+punclist+punclist2

chars = defaultdict(int)
 
def encode_to_labels(txt):
    # encoding each output word into digits
    dig_lst = []
    for index, char in enumerate(txt):
        try:
            dig_lst.append(char_list.index(char))
        except:
            print(char)
        
    return dig_lst

def find_dominant_color(image):
        #Resizing parameters
        width, height = 150,150
        image = image.resize((width, height),resample = 0)
        #Get colors from image object
        pixels = image.getcolors(width * height)
        #Sort them by count number(first element of tuple)
        sorted_pixels = sorted(pixels, key=lambda t: t[0])
        #Get the most frequent color
        dominant_color = sorted_pixels[-1][1]
        return dominant_color

def preprocess_img(img, imgSize):
    "put img into target img of size imgSize, transpose for TF and normalize gray-values"

    # there are damaged files in IAM dataset - just use black image instead
    if img is None:
        img = np.zeros([imgSize[1], imgSize[0]]) 
        print("Image None!")

    # create target image and copy sample image into it
    (wt, ht) = imgSize
    (h, w) = img.shape
    fx = w / wt
    fy = h / ht
    f = max(fx, fy)
    newSize = (max(min(wt, int(w / f)), 1),
               max(min(ht, int(h / f)), 1))  # scale according to f (result at least 1 and at most wt or ht)
    img = cv2.resize(img, newSize, interpolation=cv2.INTER_CUBIC) # INTER_CUBIC interpolation best approximate the pixels image
                                                               # see this https://stackoverflow.com/a/57503843/7338066
    most_freq_pixel=find_dominant_color(Image.fromarray(img))
    target = np.ones([ht, wt]) * most_freq_pixel  
    target[0:newSize[1], 0:newSize[0]] = img

    img = target

    return img

def counting_characters(labels):
    for label in labels:
        for char in label:
            chars[char] += 1
    return chars




In [3]:
print(char_list)
print(len(char_list))

abcdefghijklmnopqrstuvwxyz
26


In [4]:

image_list=os.listdir('content/Data-generator-for-CRNN/images/')
image_list=[filename.split(".")[0]for filename in image_list]



annot=open('content/Data-generator-for-CRNN/annotation.txt','r').readlines()
imagenames=[]
txts=[]

for cnt in annot:

    filename,txt=cnt.split('~')[0],cnt.split('~')[1].split('\n')[0]
    imagenames.append(filename)
    txts.append(txt)
    
    #print(cnt.split('~')[0])
    #print(cnt.split('~')[1].split('\n')[0])
    #print()

chars=counting_characters(txts)

c = list(zip(imagenames, txts))

random.shuffle(c)

imagenames, txts = zip(*c)


#random.shuffle(image_list)
file_train=image_list[0:int(0.75*len(image_list))]
file_test=image_list[int(0.75*len(image_list)):]

def batch_generator(filelist,n_classes,batch_size):
    while True:
        X=[]
        Y=[]
        for i in range(batch_size):
            fn=random.choice(filelist)
            img=cv2.imread(f'content/PageSegData/PageImg/{fn}.JPG',0)
            ret,img=cv2.threshold(img,150,255,cv2.THRESH_BINARY_INV)
            #print(" img=cv2.imread(f'/content/PageSegData/PageImg/{fn}.JPG',0) ",img.shape)        
            height, width = img.shape
            print ('h: ',height,'w: ', width)
            img=cv2.resize(img,(512,512))
            img=np.expand_dims(img,axis=-1)
            #img = np.stack((img,)*3, axis=-1)
            img=img/255

            seg=cv2.imread(f'content/PageSegData/PageSeg/{fn}_mask.png',1)
            seg=get_segmented_img(seg,n_classes)

            X.append(img)
            Y.append(seg)
        yield np.array(X),np.array(Y)

In [5]:

training_img = []
training_txt = []
train_input_length = []
train_label_length = []
orig_txt = []
 
#lists for validation dataset
valid_img = []
valid_txt = []
valid_input_length = []
valid_label_length = []
valid_orig_txt = []
 
max_label_len = 0

annot=open('content/Data-generator-for-CRNN/annotation.txt','r').readlines()
imagenames=[]
txts=[]

for cnt in annot:

    filename,txt=cnt.split('~')[0],cnt.split('~')[1].split('\n')[0]
    imagenames.append(filename)# nazwa pliku
    txts.append(txt)# to jaki text zawiera
    
    #print(cnt.split('~')[0])
    #print(cnt.split('~')[1].split('\n')[0])
    #print()

chars=counting_characters(txts)

c = list(zip(imagenames, txts)) # połączenie nazwy z textem

#random.shuffle(c) #wymieszanie kolejności //chociaż jak są generowane to i tak chyba bez sensu

imagenames, txts = zip(*c)
    

    
for i in range(len(imagenames)):# dla każdego obrazka
        img = cv2.imread('content/Data-generator-for-CRNN/images/'+imagenames[i],0)   
 
        img=preprocess_img(img,(128,32)) #najpierw preproces obrazu
        img=np.expand_dims(img,axis=-1)
        img = img/255.
        txt = txts[i]
        
        # compute maximum length of the text
        if len(txt) > max_label_len:
            max_label_len = len(txt)
            
        #print(img)   
        # split the 150000 data into validation and training dataset as 10% and 90% respectively
        if i%10 == 0:     
            valid_orig_txt.append(txt)   
            valid_label_length.append(len(txt))
            valid_input_length.append(31)
            valid_img.append(img)
            valid_txt.append(encode_to_labels(txt))
        else:
            orig_txt.append(txt)   
            train_label_length.append(len(txt))
            train_input_length.append(31)
            training_img.append(img)
            training_txt.append(encode_to_labels(txt)) 
        
        # break the loop if total data is 200000
        if i == 200000:
            flag = 1
            break
        i+=1
        
    
    




In [6]:
import math

annot=open('content/Data-generator-for-CRNN/annotation.txt','r').readlines()
imagenames=[]
txts=[]

for cnt in annot:

    filename,txt=cnt.split('~')[0],cnt.split('~')[1].split('\n')[0]
    imagenames.append(filename)
    txts.append(txt)
c = list(zip(imagenames, txts))

random.shuffle(c)

imagenames, txts = zip(*c)

class DataGenerator(Sequence):
    i=0
    def __init__(self, dataset,words,max_label_len,char_list, batch_size=1,dim=(1), shuffle=True):
        'Initialization'
        self.dim = dim
        self.batch_size = batch_size
        self.dataset = dataset
        self.words = words
        self.shuffle = shuffle
        self.indexes = 0
        self.max_label_len=max_label_len
        self.char_list=char_list
        self.on_epoch_end()
    
    def __len__(self):
        'Denotes the number of batches per epoch' 
        return int(np.floor(len(self.dataset) / self.batch_size))
        #return math.ceil(len(self.dataset) / self.batch_size)
        
    def __getitem__(self, index):# chyba indexuje dla batcha ale nwm
        'Generate one batch of data'
        training_img = []
        training_txt = []
        train_input_length = []
        train_label_length = []
        orig_txt = []
        
        
        img = cv2.imread('content/Data-generator-for-CRNN/images/'+imagenames[self.i],0)
        img=preprocess_img(img,(128,32))
        img=np.expand_dims(img,axis=-1)
        img = img/255.
        txt = txts[self.i]

        orig_txt.append(txt)   
        train_label_length.append(len(txt))
        train_input_length.append(31)
        training_img.append(img)
        training_txt.append(encode_to_labels(txt)) 
        print("getitem index: ",index)
            #jeśli nie nadpisuje to trzeba będzie zerować z np.array()
        train_padded_txt = pad_sequences(training_txt, maxlen=self.max_label_len, padding='post', value = len(self.char_list))
        valid_padded_txt = pad_sequences(valid_txt, maxlen=self.max_label_len, padding='post', value = len(self.char_list))
        training_img = np.array(training_img)
        train_input_length = np.array(train_input_length)
        train_label_length = np.array(train_label_length)

       # valid_img = np.array(valid_img)
       # valid_input_length = np.array(valid_input_length)
       # valid_label_length = np.array(valid_label_length)
        self.i=self.i+1
        #rint([training_img, train_padded_txt, train_input_length, train_label_length],np.zeros(len(training_img)))
        return [training_img, train_padded_txt, train_input_length, train_label_length],np.zeros(len(training_img))
         #x=[training_img, train_padded_txt, train_input_length, train_label_length]
         #y=np.zeros(len(training_img)),
    def on_epoch_end(self):
        print("Wcale sie nie zacialem: ",self.i)
   #    'Updates indexes after each epoch'
   #    self.indexes = np.arange(len(dataset))
    #   if self.shuffle == True:
     #      np.random.shuffle(self.indexes)
                     #max label len do dodania zapisane do pliku przy generowaniu i tu odczytane z pliku bedzie
train_generator = DataGenerator(dataset=imagenames,words=txts,max_label_len=20,char_list=char_list)

Wcale sie nie zacialem:  0


In [7]:
print(len(imagenames))

100000


In [8]:
print(max_label_len)

20


In [9]:
for x in char_list:
    print(x,": ",chars[x])
    

a :  80180
b :  80388
c :  80282
d :  80774
e :  81676
f :  81066
g :  81106
h :  80366
i :  80660
j :  79914
k :  80440
l :  80288
m :  81084
n :  80614
o :  80480
p :  80970
q :  80874
r :  80950
s :  80618
t :  80286
u :  80182
v :  80286
w :  79768
x :  80950
y :  81130
z :  80180


In [10]:
#pad each output label to maximum text length
 
train_padded_txt = pad_sequences(training_txt, maxlen=max_label_len, padding='post', value = len(char_list))
valid_padded_txt = pad_sequences(valid_txt, maxlen=max_label_len, padding='post', value = len(char_list))

In [11]:
inputs = Input(shape=(32,128,1))
 
# convolution layer with kernel size (3,3)
conv_1 = Conv2D(64, (3,3), activation = 'relu', padding='same')(inputs)
# poolig layer with kernel size (2,2)
pool_1 = MaxPool2D(pool_size=(2, 2), strides=2)(conv_1)
 
conv_2 = Conv2D(128, (3,3), activation = 'relu', padding='same')(pool_1)
pool_2 = MaxPool2D(pool_size=(2, 2), strides=2)(conv_2)
 
conv_3 = Conv2D(256, (3,3), activation = 'relu', padding='same')(pool_2)
 
conv_4 = Conv2D(256, (3,3), activation = 'relu', padding='same')(conv_3)
# poolig layer with kernel size (2,1)
pool_4 = MaxPool2D(pool_size=(2, 1))(conv_4)
 
conv_5 = Conv2D(512, (3,3), activation = 'relu', padding='same')(pool_4)
# Batch normalization layer
batch_norm_5 = BatchNormalization()(conv_5)
 
conv_6 = Conv2D(512, (3,3), activation = 'relu', padding='same')(batch_norm_5)
batch_norm_6 = BatchNormalization()(conv_6)
pool_6 = MaxPool2D(pool_size=(2, 1))(batch_norm_6)

 
conv_7 = Conv2D(512, (2,2), activation = 'relu')(pool_6)
 
squeezed = Lambda(lambda x: K.squeeze(x, 1))(conv_7)

# bidirectional LSTM layers with units=128
blstm_1 = Bidirectional(LSTM(128, return_sequences=True, dropout = 0.2))(squeezed)
blstm_2 = Bidirectional(LSTM(128, return_sequences=True, dropout = 0.2))(blstm_1)
 
outputs = Dense(len(char_list)+1, activation = 'softmax')(blstm_2)

# model to be used at test time
act_model = Model(inputs, outputs)

2022-05-30 08:55:44.332002: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:936] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-05-30 08:55:44.421806: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:936] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-05-30 08:55:44.422006: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:936] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-05-30 08:55:44.424082: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags

In [12]:
act_model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 32, 128, 1)]      0         
                                                                 
 conv2d (Conv2D)             (None, 32, 128, 64)       640       
                                                                 
 max_pooling2d (MaxPooling2D  (None, 16, 64, 64)       0         
 )                                                               
                                                                 
 conv2d_1 (Conv2D)           (None, 16, 64, 128)       73856     
                                                                 
 max_pooling2d_1 (MaxPooling  (None, 8, 32, 128)       0         
 2D)                                                             
                                                                 
 conv2d_2 (Conv2D)           (None, 8, 32, 256)        295168

In [13]:
labels = Input(name='the_labels', shape=[max_label_len], dtype='float32')
input_length = Input(name='input_length', shape=[1], dtype='int64')
label_length = Input(name='label_length', shape=[1], dtype='int64')
 
 
def ctc_lambda_func(args):
    y_pred, labels, input_length, label_length = args
 
    return K.ctc_batch_cost(labels, y_pred, input_length, label_length)
 
 
loss_out = Lambda(ctc_lambda_func, output_shape=(1,), name='ctc')([outputs, labels, input_length, label_length])

#model to be used at training time
model = Model(inputs=[inputs, labels, input_length, label_length], outputs=loss_out)

In [14]:
model.compile(loss={'ctc': lambda y_true, y_pred: y_pred}, optimizer = 'adam',metrics=['accuracy'])
es = EarlyStopping(monitor='val_loss', mode='min', verbose=1, patience=35) 
    
filepath='male.hdf5'
checkpoint = ModelCheckpoint(filepath=filepath, monitor='val_loss', verbose=1, save_best_only=True, mode='auto')
callbacks_list = [checkpoint,es]

In [15]:
training_img = np.array(training_img)
train_input_length = np.array(train_input_length)
train_label_length = np.array(train_label_length)

valid_img = np.array(valid_img)
valid_input_length = np.array(valid_input_length)
valid_label_length = np.array(valid_label_length)

In [16]:
#batch_size = 256
epochs = 5
history = model.fit(train_generator, 
                    epochs = epochs,validation_data = ([valid_img, valid_padded_txt, 
                    valid_input_length, valid_label_length],[np.zeros(len(valid_img))]),
                    verbose = 1, callbacks = callbacks_list)

getitem index:  0
Epoch 1/5
getitem index:  30918
getitem index:  70716


2022-05-30 08:55:51.554599: I tensorflow/stream_executor/cuda/cuda_dnn.cc:368] Loaded cuDNN version 8400
2022-05-30 08:55:53.286652: I tensorflow/core/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2022-05-30 08:55:53.934509: I tensorflow/stream_executor/cuda/cuda_blas.cc:1786] TensorFloat-32 will be used for the matrix multiplication. This will only be logged once.


     1/100000 [..............................] - ETA: 225:13:28 - loss: 78.7538 - accuracy: 0.0000e+00getitem index:  62651
getitem index:  8605
getitem index:  65828
     4/100000 [..............................] - ETA: 32:33 - loss: 52.6949 - accuracy: 0.0000e+00    getitem index:  19470
getitem index:  1768
getitem index:  93820
     7/100000 [..............................] - ETA: 34:09 - loss: 50.8502 - accuracy: 0.0000e+00getitem index:  13384
getitem index:  13665
getitem index:  36754
    10/100000 [..............................] - ETA: 36:23 - loss: 45.5379 - accuracy: 0.0000e+00getitem index:  82103
getitem index:  64416
getitem index:  89642
    13/100000 [..............................] - ETA: 37:10 - loss: 41.2699 - accuracy: 0.0000e+00getitem index:  42386
getitem index:  46969
getitem index:  18912
    16/100000 [..............................] - ETA: 36:20 - loss: 43.2283 - accuracy: 0.0000e+00getitem index:  76329
getitem index:  31099
getitem index:  51581
    19/100

   143/100000 [..............................] - ETA: 38:10 - loss: 41.1400 - accuracy: 0.0000e+00getitem index:  98100
getitem index:  21656
getitem index:  73938
   146/100000 [..............................] - ETA: 38:08 - loss: 41.0395 - accuracy: 0.0000e+00getitem index:  9057
getitem index:  68488
getitem index:  32357
   149/100000 [..............................] - ETA: 38:08 - loss: 40.8456 - accuracy: 0.0000e+00getitem index:  29048
getitem index:  48614
getitem index:  24505
   152/100000 [..............................] - ETA: 38:07 - loss: 40.8818 - accuracy: 0.0000e+00getitem index:  30427
getitem index:  76390
getitem index:  36922
   155/100000 [..............................] - ETA: 38:07 - loss: 40.8891 - accuracy: 0.0000e+00getitem index:  710
getitem index:  68614
getitem index:  776
   158/100000 [..............................] - ETA: 38:06 - loss: 41.2371 - accuracy: 0.0000e+00getitem index:  75236
getitem index:  35513
   160/100000 [............................

   289/100000 [..............................] - ETA: 37:51 - loss: 40.8080 - accuracy: 0.0000e+00getitem index:  56912
getitem index:  1928
getitem index:  70760
   292/100000 [..............................] - ETA: 37:49 - loss: 40.6500 - accuracy: 0.0000e+00getitem index:  65543
getitem index:  15901
getitem index:  7651
   295/100000 [..............................] - ETA: 37:48 - loss: 40.4654 - accuracy: 0.0000e+00getitem index:  85691
getitem index:  25608
getitem index:  32012
   298/100000 [..............................] - ETA: 37:46 - loss: 40.4322 - accuracy: 0.0000e+00getitem index:  94044
getitem index:  78279
getitem index:  64478
   301/100000 [..............................] - ETA: 37:46 - loss: 40.2586 - accuracy: 0.0000e+00getitem index:  42561
getitem index:  69735
getitem index:  62550
   304/100000 [..............................] - ETA: 37:45 - loss: 40.3511 - accuracy: 0.0000e+00getitem index:  64532
getitem index:  80678
   306/100000 [.........................

...

 99626/100000 [============================>.] - ETA: 8s - loss: 27.4812 - accuracy: 6.3237e-04getitem index:  48045
getitem index:  70868
getitem index:  63336
 99629/100000 [============================>.] - ETA: 8s - loss: 27.4813 - accuracy: 6.3235e-04getitem index:  49544
getitem index:  51371
getitem index:  13447
 99632/100000 [============================>.] - ETA: 8s - loss: 27.4809 - accuracy: 6.3233e-04getitem index:  21773
getitem index:  35681
getitem index:  63508
 99635/100000 [============================>.] - ETA: 8s - loss: 27.4803 - accuracy: 6.3231e-04getitem index:  9927
getitem index:  72401
getitem index:  75918
 99638/100000 [============================>.] - ETA: 8s - loss: 27.4804 - accuracy: 6.3229e-04getitem index:  56259
getitem index:  29204
getitem index:  46818
 99641/100000 [============================>.] - ETA: 8s - loss: 27.4800 - accuracy: 6.3227e-04getitem index:  52171
getitem index:  24621
getitem index:  22275
 99644/100000 [====================

 99773/100000 [============================>.] - ETA: 5s - loss: 27.4777 - accuracy: 6.3143e-04getitem index:  41704
getitem index:  44614
getitem index:  63032
 99776/100000 [============================>.] - ETA: 5s - loss: 27.4777 - accuracy: 6.3141e-04getitem index:  22095
getitem index:  82053
 99778/100000 [============================>.] - ETA: 5s - loss: 27.4777 - accuracy: 6.3140e-04getitem index:  20204
getitem index:  41607
getitem index:  95173
 99781/100000 [============================>.] - ETA: 4s - loss: 27.4775 - accuracy: 6.3138e-04getitem index:  47857
getitem index:  22441
getitem index:  49092
 99784/100000 [============================>.] - ETA: 4s - loss: 27.4771 - accuracy: 6.3136e-04getitem index:  33122
getitem index:  1625
getitem index:  38083
 99787/100000 [============================>.] - ETA: 4s - loss: 27.4771 - accuracy: 6.3134e-04getitem index:  48106
getitem index:  73428
getitem index:  73844
 99790/100000 [============================>.] - ETA: 4s 

 99919/100000 [============================>.] - ETA: 1s - loss: 27.4715 - accuracy: 6.4052e-04getitem index:  84786
getitem index:  33924
getitem index:  61364
 99922/100000 [============================>.] - ETA: 1s - loss: 27.4713 - accuracy: 6.4050e-04getitem index:  39494
getitem index:  75558
getitem index:  50489
 99925/100000 [============================>.] - ETA: 1s - loss: 27.4712 - accuracy: 6.4048e-04getitem index:  22794
getitem index:  40689
getitem index:  6247
 99928/100000 [============================>.] - ETA: 1s - loss: 27.4711 - accuracy: 6.4046e-04getitem index:  40415
getitem index:  40262
getitem index:  83233
 99931/100000 [============================>.] - ETA: 1s - loss: 27.4710 - accuracy: 6.4044e-04getitem index:  61961
getitem index:  30419
getitem index:  74223
 99934/100000 [============================>.] - ETA: 1s - loss: 27.4709 - accuracy: 6.4042e-04getitem index:  46639
getitem index:  9178
getitem index:  34115
 99937/100000 [=====================

2022-05-30 09:33:28.827608: W tensorflow/core/framework/op_kernel.cc:1733] UNKNOWN: IndexError: tuple index out of range
Traceback (most recent call last):

  File "/usr/local/lib/python3.8/dist-packages/tensorflow/python/ops/script_ops.py", line 271, in __call__
    ret = func(*args)

  File "/usr/local/lib/python3.8/dist-packages/tensorflow/python/autograph/impl/api.py", line 642, in wrapper
    return func(*args, **kwargs)

  File "/usr/local/lib/python3.8/dist-packages/tensorflow/python/data/ops/dataset_ops.py", line 1004, in generator_py_func
    values = next(generator_state.get_iterator(iterator_id))

  File "/usr/local/lib/python3.8/dist-packages/keras/engine/data_adapter.py", line 830, in wrapped_generator
    for data in generator_fn():

  File "/usr/local/lib/python3.8/dist-packages/keras/engine/data_adapter.py", line 956, in generator_fn
    yield x[i]

  File "/tmp/ipykernel_12500/254806788.py", line 46, in __getitem__
    img = cv2.imread('content/Data-generator-for-CRNN/

UnknownError: Graph execution error:

2 root error(s) found.
  (0) UNKNOWN:  IndexError: tuple index out of range
Traceback (most recent call last):

  File "/usr/local/lib/python3.8/dist-packages/tensorflow/python/ops/script_ops.py", line 271, in __call__
    ret = func(*args)

  File "/usr/local/lib/python3.8/dist-packages/tensorflow/python/autograph/impl/api.py", line 642, in wrapper
    return func(*args, **kwargs)

  File "/usr/local/lib/python3.8/dist-packages/tensorflow/python/data/ops/dataset_ops.py", line 1004, in generator_py_func
    values = next(generator_state.get_iterator(iterator_id))

  File "/usr/local/lib/python3.8/dist-packages/keras/engine/data_adapter.py", line 830, in wrapped_generator
    for data in generator_fn():

  File "/usr/local/lib/python3.8/dist-packages/keras/engine/data_adapter.py", line 956, in generator_fn
    yield x[i]

  File "/tmp/ipykernel_12500/254806788.py", line 46, in __getitem__
    img = cv2.imread('content/Data-generator-for-CRNN/images/

In [ ]:
# load the saved best model weights
act_model.load_weights('male.hdf5')
 
# predict outputs on validation images
prediction = act_model.predict(valid_img[10:20])
 
# use CTC decoder
out = K.get_value(K.ctc_decode(prediction, input_length=np.ones(prediction.shape[0])*prediction.shape[1],
                         greedy=True)[0][0])
 
# see the results
i = 10
for x in out:
    print("original_text = ", valid_orig_txt[i])
    print("predicted text = ", end = '')
    for p in x:  
        if int(p) != -1:
            print(char_list[int(p)], end = '')       
    print('\n')
    i+=1

In [ ]:
plt.plot(history.history['accuracy'])
plt.plot(history.history['val_accuracy'])
plt.title('Model accuracy')
plt.ylabel('Accuracy')
plt.xlabel('Epoch')
plt.legend(['Train','Validation'], loc='upper left')
plt.savefig('my_plot.png')
plt.show
